## Exercise 5 problem 2

#### Code to create an interactive map
##### Here the interactive map presents public transportation travel times to the Helsinki main railway station. The travel times are only considered inside Helsinki city borders.

In [1]:
# Importing necessary modules
import folium
from pyproj import CRS
import geopandas as gpd
import matplotlib.pyplot as plt
from geopandas.tools import geocode
import os
import numpy as np

In [2]:
# Importing traveltimes data
path = r'data/'
fn =  'TravelTimes_to_5975375_RailwayStation.shp'
fp = os.path.join(path, fn)

traveltimes = gpd.read_file(fp)
traveltimes = traveltimes[['pt_r_t', 'geometry']]
traveltimes = traveltimes.to_crs(epsg=4326)

In [3]:
# Geocoding the railway station address to be used after
stat = geocode('Kaivokatu 1, 00100 Helsinki', provider='nominatim', user_agent='autogis_xx', timeout=4)

In [4]:
# Assigning and dropping nan from traveltimes
traveltimes[traveltimes == -1] = np.nan
traveltimes = traveltimes.dropna()

In [5]:
# Importing Helsinki borders
border_fp = "data/Helsinki_borders.shp"
hel = gpd.read_file(border_fp)

In [6]:
# Helsinki borders into a correct crs
hel = hel.to_crs(crs=4326)

In [7]:
# Checking that all crs match
assert hel.crs == traveltimes.crs, "CRS differs between layers!"
assert hel.crs == stat.crs, "CRS differs between layers!"

In [8]:
# Removing grids outside of Helsinki from the traveltimes variable
traveltimes = gpd.overlay(traveltimes, hel, how='intersection')

In [9]:
# Assigning geoid column and removing unnecessary columns
traveltimes['geoid'] = traveltimes.index.astype(str)
traveltimes = traveltimes[['pt_r_t', 'geoid', 'geometry']]

In [10]:
# Taking the coordinates of our station location (to be used in plotting)
stat = stat['geometry'].bounds[['miny', 'minx']]

In [11]:
# Plotting the interactive map
# Creating a map instance
m = folium.Map(location=[60.2, 24.99],
                zoom_start=11.9, control_scale=True, prefer_canvas=True)

# Custom scale for the plot
myscale = (traveltimes['pt_r_t'].quantile((0,0.04,0.3,0.76,0.98,1))).tolist()

folium.Choropleth(
    geo_data=traveltimes,
    name='Traveltime to Helsinki railway station by public transportation',
    data=traveltimes,
    columns=['geoid', 'pt_r_t'],
    key_on='feature.id',
    fill_color='RdYlBu',
    fill_opacity=0.5,
    line_opacity=0.2,
    line_color='white', 
    line_weight=0,
    highlight=False, 
    smooth_factor=1.0,
    threshold_scale=myscale,
    legend_name= 'Traveltimes').add_to(m)

# Adding a marker at the railway station
folium.Marker(
    location=stat,
    popup='Railway station',
    icon=folium.Icon(color='green', icon='ok-sign'),
).add_to(m)

# Convert points to GeoJson to be able to see traveltime of each grid
folium.features.GeoJson(traveltimes,  
                        name='Labels',
                        style_function=lambda x: {'color':'transparent','fillColor':'transparent','weight':0},
                        tooltip=folium.features.GeoJsonTooltip(fields=['pt_r_t'],
                                                                aliases = ['Traveltime'],
                                                                labels=True,
                                                                sticky=False
                                                                            )
                       ).add_to(m)

In [12]:
m

In [14]:
# Save html map into docs folder
myfp = r'docs/'
figname ='Traveltimes_Helsinki_Railwaystation.html'
outfp = os.path.join(myfp, figname)
m.save(outfp)